In [41]:
import requests 
from bs4 import BeautifulSoup
import pandas as pd
import re
import spacy
from spacy import displacy

In [32]:
url = "https://www.rba.gov.au/publications/bulletin/2021/sep/towards-net-zero-implications-for-australia-of-energy-policies-in-east-asia.html"
response = requests.get(url)

In [33]:
soup=BeautifulSoup(response.content, "html.parser")

In [34]:
print(soup.prettify())

<!DOCTYPE html>
<html class="no-js" lang="en-au" xml:lang="en-au" xmlns="http://www.w3.org/1999/xhtml">
 <head>
  <meta content="IE=edge" http-equiv="X-UA-Compatible"/>
  <meta charset="utf-8"/>
  <!-- Google Tag Manager -->
  <script>
   (function(w,d,s,l,i){w[l]=w[l]||[];w[l].push({'gtm.start':
			new Date().getTime(),event:'gtm.js'});var f=d.getElementsByTagName(s)[0],
			j=d.createElement(s),dl=l!=='dataLayer'?'&l='+l:'';j.async=true;j.src=
			'https://www.googletagmanager.com/gtm.js?id='+i+dl;f.parentNode.insertBefore(j,f);
	})(window,document,'script','dataLayer', 'GTM-' + 'P2F2TKD' +  '');
  </script>
  <!-- End Google Tag Manager -->
  <title>
   Towards Net Zero: Implications for Australia of Energy Policies in East Asia | Bulletin – September 2021 | RBA
  </title>
  <link href="https://purl.org/dc/terms/" rel="schema.dcterms"/>
  <link href="https://agls.gov.au/agls/terms/" rel="schema.AGLSTERMS"/>
  <meta content="https://www.rba.gov.au/publications/bulletin/2021/sep/towards

In [35]:
main_content = soup.find('section')
if main_content:    
    for element in main_content(['a', 'em', 'span']):
        element.decompose()

In [48]:
text_list = []
stop_text = "growth forecast to 2050 (OECD 2018)."
    
paragraphs = main_content.find_all('p')
if paragraphs:
    for paragraph in paragraphs:
        paragraph_text = paragraph.get_text(separator=' ', strip=True)
            
        if stop_text in paragraph_text:
            text_list.append(paragraph_text)
            break
            
        text_list.append(paragraph_text)

In [49]:
df = pd.DataFrame(text_list, columns=["Paragraph Text"])
df.to_csv('10_paragraphs.csv', index=False)

In [50]:
df

Paragraph Text
0                                   16 September 2021
1   Jonathan Kemp, Madeleine McCowage and Faye\r\n...
2   China, Japan and South Korea have all set targ...
3   Global carbon emissions have risen sharply ove...
4   As parties to the Paris Agreement on climate c...
5   China, Japan and South Korea are jointly respo...
6   China is also the world's largest energy-consu...
7   Japan and South Korea have committed to achiev...
8   These emissions targets have been set with ref...
9   A range of policies have been announced by Chi...
10  China, Japan and South Korea have pledged to u...
11  All three countries are seeking to reduce the ...
12  The role of liquefied natural gas (LNG) in the...
13  While these three countries appear committed t...
14  Green hydrogen, as well as carbon capture, use...
15  The three countries have also pointed to a ran...
16  Fossil fuels account for around a quarter of A...
17  The impact of net-zero emission targets in Chi...
18  Several international bodies have explored how...
19  Importantly, the NGFS provides country-level e...
20  Each NGFS scenario includes different assumpti...
21  We use the NGFS country-level energy demand pr...
22  Under the baseline, coal exports increase grad...
23  The NDC scenario suggests countries are unlike...
24  The outlook for LNG exports is more resilient ...
25  With the global momentum towards reducing carb...
26  A number of export projects of green hydrogen ...
27  Growing global demand for electric vehicles an...
28  The overall impact of reduced fossil fuel expo...
29  The NGFS scenarios illustrate one of many poss...
30  The commitments by China, Japan and South Kore...
31  The authors are from Economic Analysis Departm...
32  South Korea's 24.4 per cent reduction by 2030 ...
33  ‘Carbon intensity of output’ is the ratio of c...
34  Korea has pledged to permanently close 30 agin...
35  South Korea's scheme covers heavy polluters in...
36  Japan is seeking to ramp up its offshore wind ...
37  Green hydrogen is a source of clean fuel produ...
38  In China, the government has mandated that ele...
39  The International Energy Association suggests ...
40  See Cunningham, Van Uffelen and Chambers (2019...
41  The NGFS is a group of over 90 central banks a...
42  Fossil fuel exports to China, Japan and South ...
43  For example, demand for Australian coal may de...
44  Geoscience Australia estimates there to be 19,...
45  This would require investment into large expan...
46  Under the Hydrogen Energy Supply Chain pilot, ...
47  For example, Fortescue Metals Group is aiming ...
48  The cumulative fall in fossil fuel exports sub...

In [39]:
nlp = spacy.load("en_core_web_sm")

In [10]:
pip install spacy

Note: you may need to restart the kernel to use updated packages.


In [11]:
pip install https://github.com/explosion/spacy-models/releases/download/en_core_web_sm-3.6.0/en_core_web_sm-3.6.0.tar.gz

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.8/12.8 MB 7.0 MB/s eta 0:00:0000:0100:01
  Preparing metadata (setup.py) ... done
Note: you may need to restart the kernel to use updated packages.


In [12]:
relationship_keywords = {'collaboration', 'cooperation', 'partner', 'engage', 
                         'support', 'fund', 'finance', 'invest', 'develop', 
                         'supply', 'promote', 'transition', 'export', 'agreement', 
                         'interest', 'share', 'enhance', 'effort', 'import'}

In [51]:
def extract_entities_and_relationships(text):
    doc = nlp(text)  # Process text with spaCy
    entities = [(ent.text, ent.label_) for ent in doc.ents if ent.label_ in ['ORG', 'GPE', 'FAC']]

    # Find relationships based on keywords
    relationships = []
    for token in doc:
        if token.lemma_ in relationship_keywords:  # Use lemma_ to check relationship keywords
            subject = [w for w in token.children if w.dep_ == "nsubj"]  # Find subject
            object_ = [w for w in token.children if w.dep_ == "dobj"]  # Find object
            if subject and object_:
                relationships.append((subject[0].text, token.text, object_[0].text))  # (subject, relationship, object)

    return entities, relationships

In [52]:
df['Entities'], df['Relationships'] = zip(*df['Paragraph Text'].apply(extract_entities_and_relationships))

In [53]:
df[['Paragraph Text', 'Entities', 'Relationships']]

Paragraph Text  \
0                                   16 September 2021   
1   Jonathan Kemp, Madeleine McCowage and Faye\r\n...   
2   China, Japan and South Korea have all set targ...   
3   Global carbon emissions have risen sharply ove...   
4   As parties to the Paris Agreement on climate c...   
5   China, Japan and South Korea are jointly respo...   
6   China is also the world's largest energy-consu...   
7   Japan and South Korea have committed to achiev...   
8   These emissions targets have been set with ref...   
9   A range of policies have been announced by Chi...   
10  China, Japan and South Korea have pledged to u...   
11  All three countries are seeking to reduce the ...   
12  The role of liquefied natural gas (LNG) in the...   
13  While these three countries appear committed t...   
14  Green hydrogen, as well as carbon capture, use...   
15  The three countries have also pointed to a ran...   
16  Fossil fuels account for around a quarter of A...   
17  The impact of net-zero emission targets in Chi...   
18  Several international bodies have explored how...   
19  Importantly, the NGFS provides country-level e...   
20  Each NGFS scenario includes different assumpti...   
21  We use the NGFS country-level energy demand pr...   
22  Under the baseline, coal exports increase grad...   
23  The NDC scenario suggests countries are unlike...   
24  The outlook for LNG exports is more resilient ...   
25  With the global momentum towards reducing carb...   
26  A number of export projects of green hydrogen ...   
27  Growing global demand for electric vehicles an...   
28  The overall impact of reduced fossil fuel expo...   
29  The NGFS scenarios illustrate one of many poss...   
30  The commitments by China, Japan and South Kore...   
31  The authors are from Economic Analysis Departm...   
32  South Korea's 24.4 per cent reduction by 2030 ...   
33  ‘Carbon intensity of output’ is the ratio of c...   
34  Korea has pledged to permanently close 30 agin...   
35  South Korea's scheme covers heavy polluters in...   
36  Japan is seeking to ramp up its offshore wind ...   
37  Green hydrogen is a source of clean fuel produ...   
38  In China, the government has mandated that ele...   
39  The International Energy Association suggests ...   
40  See Cunningham, Van Uffelen and Chambers (2019...   
41  The NGFS is a group of over 90 central banks a...   
42  Fossil fuel exports to China, Japan and South ...   
43  For example, demand for Australian coal may de...   
44  Geoscience Australia estimates there to be 19,...   
45  This would require investment into large expan...   
46  Under the Hydrogen Energy Supply Chain pilot, ...   
47  For example, Fortescue Metals Group is aiming ...   
48  The cumulative fall in fossil fuel exports sub...   

                                             Entities Relationships  
0                                                  []            []  
1                                                  []            []  
2   [(China, GPE), (Japan, GPE), (South Korea, GPE...            []  
3                                                  []            []  
4   [(the Paris Agreement, ORG), (China, GPE), (Ja...            []  
5   [(China, GPE), (Japan, GPE), (South Korea, GPE...            []  
6   [(China, GPE), (International Energy\r\n\t\t\t...            []  
7   [(Japan, GPE), (South Korea, GPE), (China, GPE...            []  
8                        [(the Paris Agreement, ORG)]            []  
9    [(China, GPE), (Japan, GPE), (South Korea, GPE)]            []  
10  [(China, GPE), (Japan, GPE), (South Korea, GPE...            []  
11   [(China, GPE), (South Korea, GPE), (China, GPE)]            []  
12  [(LNG, ORG), (LNG, ORG), (China, GPE), (LNG, O...            []  
13  [(China, GPE), (Global\r\n\t\t\t\t\t\t\tCommis...            []  
14  [(CDR, ORG), (Japan, GPE), (China, GPE), (Sout...            []  
15   [(China, GPE), (Japan, GPE), (South Korea, GPE)]            [] 

In [54]:
for index, row in df.iterrows():
    print(f"\nParagraph {index + 1}:")
    print(row['Paragraph Text'])

    # Display dependency parsing
    doc = nlp(row['Paragraph Text'])
    sentence_spans = list(doc.sents)
    displacy.render(sentence_spans, style='dep', jupyter=True, options={'compact': True})
    
    # Display named entities
    displacy.render(sentence_spans, style="ent", jupyter=True)
    
    # Print extracted entities and relationships
    print("Entities:", row['Entities'])
    print("Relationships:", row['Relationships'])


Paragraph 1:
16 September 2021


Entities: []
Relationships: []

Paragraph 2:
Jonathan Kemp, Madeleine McCowage and Faye
								Wang


Entities: []
Relationships: []

Paragraph 3:
China, Japan and South Korea have all set targets to achieve net-zero carbon emissions
								by around the middle of this century. These three countries account for around
								two-thirds of Australia's fossil fuel exports. Based on emission scenarios
								consistent with these commitments, we find that Australia's coal exports
								could decline significantly by 2050, with a more modest effect likely for
								liquefied natural gas exports; both may be offset to some degree by increases
								in green energy exports. The effect on overall Australian GDP is expected
								to be relatively small and gradual. Significant uncertainty surrounds the
								speed and manner in which countries will work to achieve net-zero emissions,
								as well as the technological developments that could change the efficiency
								and carbon intensity of fossil fuels.


/Users/loogyee/anaconda3/lib/python3.11/site-packages/spacy/displacy/__init__.py:213: UserWarning: [W006] No entities to visualize found in Doc object. If this is surprising to you, make sure the Doc was processed using a model that supports named entity recognition, and check the `doc.ents` property manually if necessary.
  warnings.warn(Warnings.W006)


Entities: [('China', 'GPE'), ('Japan', 'GPE'), ('South Korea', 'GPE'), ('Australia', 'GPE'), ('Australia', 'GPE')]
Relationships: []

Paragraph 4:
Global carbon emissions have risen sharply over the past 150 years. The
							major driver of this increase has been the rise in global energy use. Over
							the past 50 years, the world's energy supply has more than doubled,
							and in recent years the share generated by fossil fuels – the major
							source of carbon emissions – has accounted for around 80 per cent
							(Graph 1).


...

Entities: [('Geoscience Australia', 'ORG')]
Relationships: []

Paragraph 46:
This would require investment into large expansions of Australia's current
									LNG export capacity.


Entities: [('Australia', 'GPE'), ('LNG', 'ORG')]
Relationships: []

Paragraph 47:
Under the Hydrogen Energy Supply Chain pilot, hydrogen produced from brown
									coal in Victoria's Latrobe Valley will be exported to Japan via a special
									vessel, with first shipments of liquefied hydrogen expected in October and
									March 2022 following -related delays (Department of Industry, Science, Energy
									and Resources 2021).


Entities: [('the Hydrogen Energy Supply Chain', 'ORG'), ('Victoria', 'GPE'), ('Japan', 'GPE'), ('Department of Industry, Science, Energy\r\n\t\t\t\t\t\t\t\t\tand Resources', 'ORG')]
Relationships: []

Paragraph 48:
For example, Fortescue Metals Group is aiming to build Australia's first
									green steel project in the Pilbara, powered entirely by green hydrogen from
									local wind and solar in the next few years (Forrest 2021).


Entities: [('Fortescue Metals Group', 'ORG'), ('Australia', 'GPE')]
Relationships: []

Paragraph 49:
The cumulative fall in fossil fuel exports subtracts around 3 per cent
									off the level of GDP in 2050 relative to the baseline. Assumes real GDP
									to grow in line with RBA forecasts to 2023 (RBA 2021), then at the OECD's
									growth forecast to 2050 (OECD 2018).


Entities: [('RBA', 'ORG'), ('OECD', 'ORG'), ('OECD', 'ORG')]
Relationships: []


In [55]:
entity1_list = []
relationship_list = []
entity2_list = []
date_list = []
money_list = []

In [56]:
# Iterate through each paragraph
for index, row in df.iterrows():
    doc = nlp(row['Paragraph Text'])  # Process the paragraph with spaCy

    for sent in doc.sents:
        # Extract named entities (countries, organizations)
        entities = []
        money_in_sentence = []

        for ent in sent.ents:
            if 'Inititative' in ent.text.lower(): 
                ent = ent._replace(label_='POL')
                entities.append(ent)
            elif ent.label_ in ['GPE', 'ORG', 'POL', 'MONEY']:
                entities.append(ent)

            # Collect monetary amounts
            if ent.label_ == "MONEY":
                money_in_sentence.append(ent.text)
        
        # Look for verbs or specific relationship nouns in the sentence
        verbs = [token for token in sent if token.pos_ == "VERB"]
        keywords_in_sentence = [token.text for token in sent if token.lemma_ in relationship_keywords]
        
        # Extract dates
        dates = [ent.text for ent in sent.ents if ent.label_ == "DATE"]

        # If we find two entities and a relationship keyword, we assume a relationship
        if len(entities) >= 2 and keywords_in_sentence:
            entity1_list.append(entities[0].text)

            # Concatenate the relationship noun and verb (if available) into one string
            relationship_info = keywords_in_sentence[0]
            if verbs:
                relationship_info += " (verb: " + verbs[0].lemma_ + ")"

            relationship_list.append(relationship_info)  # Store concatenated info
            entity2_list.append(entities[1].text)
            date_list.append(dates[0] if dates else "n/a")
            money_list.append(money_in_sentence[0] if money_in_sentence else "n/a")

In [57]:
# DataFrame
relationships_df = pd.DataFrame({
    "Entity1": entity1_list,
    "Relationship": relationship_list,
    "Entity2": entity2_list,
    "Date": date_list,
    "Money": money_list
})

In [58]:
relationships_df

Entity1                Relationship  \
0                          Australia                      export   
1                              China       supplied (verb: mean)   
2                              China   developing (verb: pledge)   
3                              Japan          share (verb: look)   
4                              Japan      share (verb: announce)   
5                              Japan          share (verb: make)   
6                              Japan     efforts (verb: develop)   
7                          Australia     exports (verb: account)   
8                          Australia    exports (verb: comprise)   
9                          Australia    exports (verb: estimate)   
10                             China                     exports   
11                              NGFS  transition (verb: provide)   
12                              NGFS         exports (verb: use)   
13                             China        exports (verb: fall)   
14                               NDC      exports (verb: remain)   
15                               NDC    exports (verb: increase)   
16      the Western Green Energy Hub      export (verb: propose)   
17                             China     exports (verb: achieve)   
18                       Van Uffelen         exports (verb: see)   
19                              NGFS       share (verb: include)   
20                             China   exports (verb: calibrate)   
21                             China   Exports (verb: calibrate)   
22                         Australia      export (verb: require)   
23  the Hydrogen Energy Supply Chain    exported (verb: produce)   

         Entity2                Date         Money  
0      Australia                 n/a           n/a  
1          China                2018           n/a  
2          Japan                 n/a           n/a  
3    South Korea                2030           n/a  
4            LNG                2030           n/a  
5    South Korea                 n/a           n/a  
6          China                 n/a           n/a  
7          Japan    around a quarter           n/a  
8            LNG                 n/a           n/a  
9            LNG                 n/a           n/a  
10         Japan                 n/a           n/a  
11         China                 n/a           n/a  
12     Australia                 n/a           n/a  
13         Japan         mid-century           n/a  
14         China  the current decade           n/a  
15           LNG                2020           n/a  
16  $100 billion                 n/a  $100 billion  
17         Japan         mid-century           n/a  
18      Chambers                2019           n/a  
19           RBA                 n/a           n/a  
20         Japan                 n/a           n/a  
21         Japan                 n/a           n/a  
22           LNG                 n/a           n/a  
23      Victoria             October           n/a

In [59]:
# Export to csv
relationships_df.to_csv('10_relationships.csv', index=False)